In [2]:
#general computations packages
import numpy as np 
import requests
import pandas as pd
import json
import geopandas as gpd
import datetime
import io
#API packages 
import requests
from shapely.geometry import Point
np.random.seed(42)


#data visualization packages
from matplotlib import pyplot as plt
import folium
from folium.plugins import HeatMap
import osmnx as ox
import networkx as nx
import plotly.offline as py
import plotly.graph_objs as go
#py.init_notebook_mode(connected=False)

In [3]:
%%html
<meta charset="utf-8">
<head>
  <title>Geo (spinning))</title>
</head>

<style>
body {
  font-family: "Helvetica Neue", Helvetica, sans-serif;
  font-size: 14px;
  color: #333;
}

path {
  fill: #87B687;
  stroke: #777;
}
#content {
  background-color:#283A60;
}

#content-tag {
  float: right;
  text-align: left;
  margin-right: 340px;
  margin-top: -460px;
  color: #fff;
  font-family: avenir;
  font-size: 2rem;
}

</style>

<body>
  <div id="content" >
    <canvas width="800" height="600" style="margin-left: -100px;"></canvas>
  </div>
  <div id="content-tag">
    <span style="color=#000;"> <h1> THE GREAT <br> EARTHQUAKES</h1></span>
  </div>

  <script src="https://cdnjs.cloudflare.com/ajax/libs/d3/4.2.2/d3.min.js"></script>
  <script src="https://unpkg.com/topojson@3"></script>
  <script src="http://d3js.org/queue.v1.min.js"></script>

  <script>
      var geojson = {}
      var sphere = ({type: "Sphere"})
      var land = {}
      var Equakes ={}


      var context = d3.select('#content canvas')
        .node()
        .getContext('2d');

      var projection = d3.geoOrthographic()
        .scale(180);

      var geoGenerator = d3.geoPath()
        .projection(projection)
        .pointRadius(4)
        .context(context);

      var yaw = 300;


      function magnitudeRadius() {
        var scale = d3.scaleSqrt().domain([0, 100]).range([0, 6]);
        return function(quake) {
          return scale((Math.exp(quake.properties.mag)));
        }
      }


      function update() {
        projection.rotate([yaw, 0])

        context.clearRect(0, 0, 800, 800);

        context.lineWidth = 1.5;
        context.fillStyle = "#283A60";
        context.beginPath(),geoGenerator(sphere), context.fill(), context.stroke();


        context.lineWidth = 0.2;
        context.strokeStyle = '#333';
        context.fillStyle="#000";
        context.beginPath();
        geoGenerator(land),
        context.fill();
        context.stroke();
          

        const color = d3.color('#ffba00');
        color.opacity = 0.25;
        context.fillStyle = color;
        var circles = Equakes.features;
        geoGenerator.pointRadius(magnitudeRadius());
        Equakes.features.forEach(d => {context.beginPath(), geoGenerator(d), context.fill();});
        geoGenerator.pointRadius(null);
        yaw += 3
      }
    
        d3.json('https://unpkg.com/world-atlas@1/world/110m.json', function(err, json) {
        geojson = json;
        land = topojson.feature(geojson, geojson.objects.countries)
      })
    

      d3.json('https://earthquake.usgs.gov/earthquakes/feed/v1.0/summary/2.5_month.geojson', function(err, quakes) {
        Equakes = quakes;
        window.setInterval(update, 100);
      })


  </script>
</body>

In [2]:
api="https://earthquake.usgs.gov/fdsnws/event/1/query?format=geojson&starttime=2008-01-01&endtime=2018-12-31&minmagnitude=3&minlat=24.6&maxlat=50&minlon=-125&maxlon=-65&limit=20000"
r = requests.get(api)
d =json.loads(r.text)
temp = []

for i in d['features']:
        ID = i['id']
        Long,Lat,Depth = i['geometry']['coordinates']
        Magnitude = i['properties']['mag']
        CDI = i['properties']['cdi']
        Time = datetime.datetime.utcfromtimestamp(i['properties']['time']/1000)
        Sig = i['properties']['sig']
        RMS = i['properties']['rms']
        Tsn = i['properties']['tsunami']
        temp.append([ID,Long, Lat, Depth, Magnitude,CDI,Time,Sig,RMS,Tsn])
        
# create a dataframe and save
col_names = ['ID','Long', 'Lat', 'Depth', 'Magnitude','CDI','Time','Sig','RMS','Tsn']
features = pd.DataFrame(temp, columns=col_names)
geometry = [Point(xy) for xy in zip(features['Long'], features['Lat'])]

features= gpd.GeoDataFrame(features,crs={'init' :'epsg:4326'}, geometry=geometry)

In [4]:
feat1 = features[features['Magnitude']>5]
feat2=features[features['Magnitude']<4.99]

In [5]:
# let's center the map on Philadelphia
m = folium.Map(
    location=[41.865205, -87.625429],
    zoom_start=4,
    tiles='https://api.mapbox.com/styles/v1/dhruvs04/cjlei44jg06r52rpd0l6m1p81/tiles/256/{z}/{x}/{y}@2x?access_token=pk.eyJ1IjoiZGhydXZzMDQiLCJhIjoiY2psZWkxem45MDZuNjNrcWhkZDMxdXo5byJ9.O_pXu61MgF8AfZiWLaR5pA',
    API_key='pk.eyJ1IjoiZGhydXZzMDQiLCJhIjoiY2psZWkxem45MDZuNjNrcWhkZDMxdXo5byJ9.O_pXu61MgF8AfZiWLaR5pA',
    attr='My Data Attribution'
)

# add the GeoJson to the map
for i in range(0,len(feat2)):
    folium.Circle([feat2.iloc[i]['Lat'], feat2.iloc[i]['Long']],
                  radius=feat2.iloc[i]['Magnitude']*2,
                  weight= 1,
                  opacity= 1,
                  color='#2c84f0',
                  fill=True,
                  fill_color='#2c84f0',
                  fill_opacity=0.2).add_to(m)
    
for i in range(0,len(feat1)):
    folium.Circle([feat1.iloc[i]['Lat'], feat1.iloc[i]['Long']],
                  radius=feat1.iloc[i]['Magnitude']**6,
                  weight= 1,
                  opacity= 1,
                  color='#a626fb',
                  fill=True,
                  fill_color='#a626fb',
                  fill_opacity=0.2).add_to(m)

# also add option to toggle layers

m  

In [7]:
coordinates = features[['Lat','Long']].values

# add heat map
m = folium.Map(
    location=[37.364942, -121.520455],
    zoom_start=7,
    tiles='https://api.mapbox.com/styles/v1/dhruvs04/cjlei44jg06r52rpd0l6m1p81/tiles/256/{z}/{x}/{y}@2x?access_token=pk.eyJ1IjoiZGhydXZzMDQiLCJhIjoiY2psZWkxem45MDZuNjNrcWhkZDMxdXo5byJ9.O_pXu61MgF8AfZiWLaR5pA',
    API_key='pk.eyJ1IjoiZGhydXZzMDQiLCJhIjoiY2psZWkxem45MDZuNjNrcWhkZDMxdXo5byJ9.O_pXu61MgF8AfZiWLaR5pA',
    attr='My Data Attribution'
)

HeatMap(coordinates).add_to(m)


m

Exploring the Norther California 

In [8]:
headers = {
    'Pragma': 'no-cache',
    'Origin': 'http://ncedc.org',
    'Accept-Encoding': 'gzip, deflate',
}

data = {
  'format': 'nccsv',
  'mintime': '1967/01/01,00:00:00',
  'maxtime': '',
  'minmag': '2.5',
  'maxmag': '',
  'mindepth': '',
  'maxdepth': '',
  'minlat': '',
  'maxlat': '',
  'minlon': '',
  'maxlon': '',
  'etype': 'E',
  'keywds': '',
  'outputloc': 'web',
  'searchlimit': '1000000'
}

response = requests.post('http://www.ncedc.org/cgi-bin/catalog-search2.pl', headers=headers, data=data)

In [9]:
d=response.text[290:-22]

In [10]:
df = pd.read_csv(io.StringIO(d))

In [11]:
geometry = [Point(xy) for xy in zip(df['Longitude'], df['Latitude'])]

df= gpd.GeoDataFrame(df,crs={'init' :'epsg:4326'}, geometry=geometry)

In [12]:
df.head()

DateTime  Latitude  Longitude   Depth  Magnitude MagType  \
0  1967/08/01 10:33:50.47  36.08000 -121.07083  80.339        2.5      Mx   
1  1967/08/02 02:49:12.55  35.63433 -120.75716   3.980        2.6      Mx   
2  1967/08/03 05:55:26.73  36.37967 -121.00850  39.609        2.7      Mx   
3  1967/08/03 06:57:01.25  36.39550 -121.01667  40.159        2.7      Mx   
4  1967/08/03 20:21:26.52  36.54350 -121.17216   5.945        2.6      Mx   

   NbStations  Gap  Distance   RMS Source  EventID  \
0          10  292        42  0.25   NCSN  1000872   
1           9  322       108  0.24   NCSN  1000887   
2          10  298        21  0.41   NCSN  1000912   
3          10  293        19  0.46   NCSN  1000916   
4          10  132         6  0.07   NCSN  1000926   

                      geometry  
0     POINT (-121.07083 36.08)  
1  POINT (-120.75716 35.63433)  
2   POINT (-121.0085 36.37967)  
3   POINT (-121.01667 36.3955)  
4   POINT (-121.17216 36.5435)

In [27]:
df['date'] = pd.to_datetime(df['DateTime'],unit='ns')
df['year']= df['date'].dt.year
df['month']= df['date'].dt.month
len(df)

55830

In [28]:

df.head()

DateTime  Latitude  Longitude   Depth  Magnitude MagType  \
0  1967/08/01 10:33:50.47  36.08000 -121.07083  80.339        2.5      Mx   
1  1967/08/02 02:49:12.55  35.63433 -120.75716   3.980        2.6      Mx   
2  1967/08/03 05:55:26.73  36.37967 -121.00850  39.609        2.7      Mx   
3  1967/08/03 06:57:01.25  36.39550 -121.01667  40.159        2.7      Mx   
4  1967/08/03 20:21:26.52  36.54350 -121.17216   5.945        2.6      Mx   

   NbStations  Gap  Distance   RMS Source  EventID  \
0          10  292        42  0.25   NCSN  1000872   
1           9  322       108  0.24   NCSN  1000887   
2          10  298        21  0.41   NCSN  1000912   
3          10  293        19  0.46   NCSN  1000916   
4          10  132         6  0.07   NCSN  1000926   

                      geometry                    date  year  month  
0     POINT (-121.07083 36.08) 1967-08-01 10:33:50.470  1967      8  
1  POINT (-120.75716 35.63433) 1967-08-02 02:49:12.550  1967      8  
2   POINT (-121.0085 36.37967) 1967-08-03 05:55:26.730  1967      8  
3   POINT (-121.01667 36.3955) 1967-08-03 06:57:01.250  1967      8  
4   POINT (-121.17216 36.5435) 1967-08-03 20:21:26.520  1967      8

In [29]:
to_skip = ['Latitude',  'Longitude',  'year', 'date', 'DateTime','Source',"EventID","geometry",'month']
main_columns = [x for x in df.columns if x not in to_skip]
main_columns

['Depth', 'Magnitude', 'MagType', 'NbStations', 'Gap', 'Distance', 'RMS']

In [30]:
dff = df[df['year'] == 2015]

In [31]:
dfmax = df.groupby('year', as_index=False)[
    'Depth', 'Magnitude', 'Distance', 'Gap'].min()

In [32]:
year_value = 2010

In [33]:
GREEN_RED = [
    [0.0, 'rgb(83, 153, 15)'],
    [0.1111111111111111, 'rgb(42, 195, 23)'],
    [0.2222222222222222, 'rgb(19, 197, 67)'],
    [0.3333333333333333, 'rgb(119, 229, 34)'],
    [0.4444444444444444, 'rgb(161, 243, 27)'],
    [0.5555555555555556, 'rgb(210, 220, 20)'],
    [0.6666666666666666, 'rgb(202, 194, 27)'],
    [0.7777777777777778, 'rgb(215, 135, 36)'],
    [0.8888888888888888, 'rgb(220, 91, 24)'],
    [1.0, 'rgb(205, 23, 23)']
]

color_scale = GREEN_RED

In [36]:
mapbox_access_token = 'pk.eyJ1IjoiaXZhbm5pZXRvIiwiYSI6ImNqNTU0dHFrejBkZmoycW9hZTc5NW42OHEifQ._bi-c17fco0GQVetmZq0Hw'

In [38]:
dff = df[df['year'] == year_value]

    # Paint mapbox into the data
data = [
        go.Scattermapbox(
            lat=dff['Latitude'],
            lon=dff['Longitude'],
            mode='markers',
            marker=go.scattermapbox.Marker(
                size=(dff['Magnitude']**2.5),
                colorscale=color_scale,
                cmin=dff['Magnitude'].min(),
                color=dff['Magnitude'],
                cmax=dff['Magnitude'].max(),
                colorbar=dict(
                    title='Magnitude'
                ),
                opacity=0.5
            )
        )
    ]

    # Layout and mapbox properties
layout = go.Layout(
        autosize=True,
        hovermode='closest',
        showlegend=False,
        mapbox=go.layout.Mapbox(
            accesstoken=mapbox_access_token,
            bearing=0,
            center=go.layout.mapbox.Center(
            lat=37.437,
            lon=-119.451
        ),
            pitch=0,
            zoom=4,
            style='dark'
        ),
        paper_bgcolor='#191a1a',
        plot_bgcolor='#191a1a',
    )
fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='Earthquakes')

In [39]:
xaxis_value='Magnitude'
yaxis_value='Depth'

In [40]:

dff = df[df['year'] == year_value]
data = [
        go.Scatter(
            x=dff[xaxis_value],
            y=dff[yaxis_value],
            mode='markers',
            marker={
                'symbol': 'circle',
                'size': dff['Magnitude']**2,
                'color': 'rgb(248, 177, 149)'
            }
        )
    ]

layout = go.Layout(
        autosize=True,
        xaxis={
            'color': '#FFF',
            'autorange': True,
            'title': xaxis_value,
            'showspikes': True
        },
        yaxis={
            'color': '#FFF',
            'autorange': True,
            'title': yaxis_value,
        },
        margin={'l': 40, 'b': 40, 't': 10, 'r': 0},
        hovermode='closest',
        paper_bgcolor='#191a1a',
        plot_bgcolor='#191a1a',
    )

fig = go.Figure(data=data, layout=layout)
py.iplot(fig, filename='Nuclear Waste Sites on American Campuses')

In [41]:
traces = []
marker_color = ''

for year in df['year'].unique():
    if year > 2003:
        dff = df[df['year'] == year]
    if(year == year_value):
        marker_color = '#C2FF0A'
    elif year_value >= 2003:
          marker_color = '#FF0A47'        
    traces.append(go.Box(
        y=round(dff['Depth'],2),
        name=str(year),
        boxpoints='all',
        jitter=0.5,
        whiskerwidth=0.2,
        fillcolor=marker_color,
        marker=dict(
            size=2,
        ),
        line=dict(color=marker_color, width=1),
    ))
    
layout = go.Layout(
        yaxis=dict(
            title='year',
            autorange=True,
            zeroline=True,
            gridwidth=1,
            zerolinecolor='rgb(255, 255, 255)',
            zerolinewidth=2,
        ),
        hoverlabel={
            'bgcolor': '#FFF',
            'font': {
                'color': 'black'
            },
        },
        margin={'l': 40, 'b': 40, 't': 10, 'r': 0},
        hovermode='closest',
        paper_bgcolor='#191a1a',
        plot_bgcolor='#191a1a',
    )
fig = go.Figure(data=traces, layout=layout)
py.iplot(fig)